# browser

> Contains the GenomeBrowser class

In [ ]:
#| hide
%load_ext autoreload
%autoreload 2

In [ ]:
#| default_exp browser

In [ ]:
#| hide
from nbdev.showdoc import *


In [ ]:
#| export
from fastcore.basics import *

from genomenotebook.utils import (
    get_genome_annotations,
    get_gene_patches, 
    get_genes_from_annotation, 
    create_genome_browser_plot,
    get_all_glyphs)

from genomenotebook.javascript import (
    x_range_change_callback_code, 
    search_callback_code, 
)
from bokeh.models import (
    CustomJS,
    Range1d,
    ColumnDataSource,
    AutocompleteInput,
    Rect,
    Div,
    Styles
)
from bokeh.plotting import show
from bokeh.layouts import column

from Bio import SeqIO

import itertools
    
import warnings

In [ ]:
#| export
class GenomeBrowser:
    """Initialize a GenomeBrowser object."""
    def __init__(self,
                 genome_path: str, #path to the fasta file of the genome sequence
                 gff_path: str, #path to the gff3 file of the annotations
                 seq_id: str = None, #id of the sequence to show for genomes with multiple contigs
                 init_pos: int = None, #initial position to display
                 init_win: int = 10000, #initial window size (max=20000)
                 bounds: tuple = None, #bounds can be specified. This helps preserve memory by not loading the whole genome if not needed.
                 show_seq: bool = True, #shows the sequence when zooming in
                 search: bool = True, #enables a search bar to lookup a gene name or a DNA sequence
                 **kwargs):
        
        self.genome_path = genome_path
        self.gff_path = gff_path
        self.rec = self._get_sequence_record(seq_id)            
        self.seq_len = len(self.rec.seq) #length of the reference sequence before bounds are applied
        self._apply_bounds(bounds)
        self._set_init_pos(init_pos)

        self.init_win = min(init_win,self.bounds[1]-self.bounds[0])

        self.show_seq = show_seq
        self.max_glyph_loading_range = 20000
        self.frame_width = 600

        self.elements = self._get_browser(**kwargs)
        if search:
            self.elements = [self._get_search_box()]+self.elements
            
        self.tracks=[] 
    
    
    def _set_init_pos(self, init_pos):
        if init_pos == None:
            self.init_pos=sum(self.bounds)//2
        elif init_pos>self.bounds[1] or init_pos<self.bounds[0]:
            warnings.warn("Requested an initial position outside of the browser bounds")
            self.init_pos=sum(self.bounds)//2
        else:
            self.init_pos=init_pos
    
    def _apply_bounds(self, bounds):
        if bounds == None:
            self.bounds=(0,self.seq_len)
        else:
            self.bounds=bounds
        
        self.rec.seq=self.rec.seq[self.bounds[0]:self.bounds[1]]

    def _get_sequence_record(self, seq_id):
        if seq_id==None: #when no seq_id is provided we take the first element
            rec = next(SeqIO.parse(self.genome_path, 'fasta'))
        else:
            rec_found=False
            for rec in SeqIO.parse(self.genome_path, 'fasta'):
                if rec.id==seq_id:
                    rec_found=True
                    break
            
            if not rec_found:
                warnings.warn("seq_id not found in fasta file")
        return rec

    def _get_browser(self, **kwargs):

        semi_win = self.init_win / 2
        x_range = Range1d(
            max(self.bounds[0],self.init_pos - semi_win), min(self.bounds[1],self.init_pos + semi_win), 
            bounds=self.bounds, 
            max_interval=100000,
            min_interval=40
        )
        
        annotation = get_genome_annotations(self.gff_path,
                                            seq_id = self.rec.id,
                                            bounds = self.bounds)
        
        genes = get_genes_from_annotation(annotation) 
        
        #This contains the glyphs plotted by bokeh
        self.glyph_source = ColumnDataSource(get_gene_patches(genes, x_range.start, x_range.end))

        #This contains the positions of the glyphs plotted by bokeh
        self.loaded_range = ColumnDataSource({"start":[x_range.start],
                                                "end":[x_range.end], 
                                                "range":[self.max_glyph_loading_range]})

        #This contains the glyphs for the whole genome
        self.all_glyphs=get_all_glyphs(genes, self.bounds)

        p = create_genome_browser_plot(self.glyph_source, 
                                       x_range, **kwargs)
        p.frame_width=self.frame_width

        sty=Styles(font_size='14px',
                font_family="Courrier",
                color="black",
                display="inline-block",
                background_color = "white",
                margin="0",
                margin_left= "2px",
                )
        
        ## Adding the ability to display the sequence when zooming in
        sequence = {
            'seq': str(self.rec.seq).upper(),
            'bounds':self.bounds
        }

        self.div = Div(height=18, height_policy="fixed", 
                    width=600, width_policy="fixed",
                    styles = sty
                    )
        
        xcb = CustomJS(
            args={
                "x_range": p.x_range,
                "sequence": sequence,
                "all_glyphs":self.all_glyphs,
                "glyph_source": self.glyph_source,
                "div": self.div,
                "loaded_range":self.loaded_range,
            },
            code=x_range_change_callback_code
        )

        p.x_range.js_on_change('start', xcb)
        self.x_range=p.x_range
        self.gene_track=p

        if self.show_seq:
            return [p,self.div]
        else:
            return [p]
        
    def _get_search_box(self):
        ## Create a text input widget for search
        text_input = AutocompleteInput(completions=self.all_glyphs["names"], value="")

        ## Adding BoxAnnotation to highlight search results
        search_span_source = ColumnDataSource({"x":[],"width":[]})#"y":[]
        h=Rect(x='x',y=-2,width='width',height=self.gene_track.height,fill_color='green',fill_alpha=0.2,line_alpha=0)
        self.gene_track.add_glyph(search_span_source, h)

        call_back_search = CustomJS(
            args={
                "x_range": self.x_range,
                "glyph_source": self.glyph_source,
                "bounds": self.bounds,
                "all_glyphs": self.all_glyphs,
                "loaded_range": self.loaded_range,
                "text_input": text_input,
                "search_span_source": search_span_source,
                "div": self.div,
            },
            code=search_callback_code
        )

        text_input.js_on_change('value',call_back_search)#,xcb)

        return text_input
    
    def show(self):
        show(column(self.elements + [t.fig for t in self.tracks]))



In [ ]:
#| hide
from genomenotebook.javascript import get_js_code

In [ ]:
#| hide
#Useful for javascript development as it is not autmatically reimported 
x_range_change_callback_code = get_js_code("x_range_change_callback_code.js")
search_callback_code = get_js_code("search_callback_code.js")

In [ ]:
from genomenotebook.data import get_example_data_dir
import os

In [ ]:
data_path = get_example_data_dir()
genome_path = os.path.join(data_path, "GCA_000189435.3_ASM18943v3_genomic.fna")
gff_path = os.path.join(data_path, "GCA_000189435.3_ASM18943v3_genomic.gff")

g=GenomeBrowser(genome_path=genome_path, gff_path=gff_path, init_pos=10000)
g.show()


In [ ]:
#| hide
#Testing svg output
g=GenomeBrowser(genome_path=genome_path, gff_path=gff_path, bounds=(2000,5000), output_backend="svg")
g.show()

In [ ]:
#| hide
#Testing out of bounds warning and seq_id warning
g=GenomeBrowser(genome_path=genome_path, gff_path=gff_path, init_pos=10000, bounds=(2000,5000), seq_id="AF")
g.show()

/tmp/ipykernel_5681/2790093912.py:63: UserWarning: seq_id not found in fasta file
  warnings.warn("seq_id not found in fasta file")
/tmp/ipykernel_5681/2790093912.py:39: UserWarning: Requested an initial position outside of the browser bounds
  warnings.warn("Requested an initial position outside of the browser bounds")


#### Visualising multiple contigs

In [ ]:
genome_path = os.path.join(data_path, "jmh43.fna")
gff_path = os.path.join(data_path, "jmh43.gff")

for rec in itertools.islice(SeqIO.parse(genome_path,"fasta"),5):
    
    g=GenomeBrowser(genome_path=genome_path, 
                    gff_path=gff_path, 
                    seq_id=rec.id, 
                    search=False)
    g.show()

Showing the same data as vertical bars

In [ ]:
#| export
from genomenotebook.track import Track

In [ ]:
#| export
@patch
def add_track(self:GenomeBrowser,
             height:int = 200, #size of the track
             output_backend="webgl", #can be set to webgl (more efficient) or svg (for figure export)
             ) -> Track:
    """Adds a track to the GenomeBrowser. Ensures that the x_range are shared and figure widths are identical."""
    t = Track(height=height, 
              output_backend=output_backend)
    t.fig.x_range = self.x_range
    t.fig.frame_width = self.frame_width
    t.bounds = self.bounds
    t.loaded_range = ColumnDataSource(self.loaded_range.data)
    t.max_glyph_loading_range = self.max_glyph_loading_range
    self.tracks.append(t)
    return t
    

In [ ]:
#| hide
import nbdev; nbdev.nbdev_export()